In [ ]:
!pip install opencv-python
!pip install -q transformers
!pip install -q sentencepiece
!pip install -q jiwer
!pip install -q datasets
!pip install -q evaluate
!pip install -q -U accelerate

!pip install -q matplotlib
!pip install -q protobuf==3.20.1
!pip install -q tensorboard
!pip install elementpath
!pip install scikit-learn
!pip install numpy==1.26.4
!pip install transformers==4.45.2
!pip install git+https://github.com/huggingface/transformers@muellerzr-more-models-sadface
# !pip install transformers==4.49.0.dev0
# !pip install tokenizers==0.21.0

ERROR: Ignored the following yanked versions: 4.14.0, 4.25.0, 4.46.0
ERROR: Could not find a version that satisfies the requirement transformers==4.49.0.dev0 (from versions: 0.1, 2.0.0, 2.1.0, 2.1.1, 2.2.0, 2.2.1, 2.2.2, 2.3.0, 2.4.0, 2.4.1, 2.5.0, 2.5.1, 2.6.0, 2.7.0, 2.8.0, 2.9.0, 2.9.1, 2.10.0, 2.11.0, 3.0.0, 3.0.1, 3.0.2, 3.1.0, 3.2.0, 3.3.0, 3.3.1, 3.4.0, 3.5.0, 3.5.1, 4.0.0rc1, 4.0.0, 4.0.1, 4.1.0, 4.1.1, 4.2.0, 4.2.1, 4.2.2, 4.3.0rc1, 4.3.0, 4.3.1, 4.3.2, 4.3.3, 4.4.0, 4.4.1, 4.4.2, 4.5.0, 4.5.1, 4.6.0, 4.6.1, 4.7.0, 4.8.0, 4.8.1, 4.8.2, 4.9.0, 4.9.1, 4.9.2, 4.10.0, 4.10.1, 4.10.2, 4.10.3, 4.11.0, 4.11.1, 4.11.2, 4.11.3, 4.12.0, 4.12.1, 4.12.2, 4.12.3, 4.12.4, 4.12.5, 4.13.0, 4.14.1, 4.15.0, 4.16.0, 4.16.1, 4.16.2, 4.17.0, 4.18.0, 4.19.0, 4.19.1, 4.19.2, 4.19.3, 4.19.4, 4.20.0, 4.20.1, 4.21.0, 4.21.1, 4.21.2, 4.21.3, 4.22.0, 4.22.1, 4.22.2, 4.23.0, 4.23.1, 4.24.0, 4.25.1, 4.26.0, 4.26.1, 4.27.0, 4.27.1, 4.27.2, 4.27.3, 4.27.4, 4.28.0, 4.28.1, 4.29.0, 4.29.1, 4.29.2, 4.30.0, 4.30

  Using cached tokenizers-0.21.0-cp39-abi3-win_amd64.whl.metadata (6.9 kB)
Using cached tokenizers-0.21.0-cp39-abi3-win_amd64.whl (2.4 MB)
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.20.3
    Uninstalling tokenizers-0.20.3:
      Successfully uninstalled tokenizers-0.20.3


ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
transformers 4.45.2 requires tokenizers<0.21,>=0.20, but you have tokenizers 0.21.0 which is incompatible.


In [2]:
import os
import numpy as np
import pandas as pd
import glob as glob
import matplotlib.pyplot as plt
from PIL import Image

block_plot = False
plt.rcParams['figure.figsize'] = (12, 9)
bold = f"\033[1m"
reset = f"\033[0m"

In [40]:
from xml.etree import ElementTree as ET

def get_text_regions(xml_file):
    try:
        tree = ET.parse(xml_file)
        root = tree.getroot()

        namespaces = {'ns': root.tag.split('}')[0].strip('{')}

        page_elem = root.find(".//ns:Page", namespaces)
        image_filename = page_elem.attrib.get("imageFilename")

        regions = []

        for region in root.findall(".//ns:TextRegion", namespaces):

            for textline in region.findall(".//ns:TextLine", namespaces):
                text_id = textline.attrib.get("id")
                # text_coords = textline.find(".//ns:Coords", namespaces).get('points')
                # unicode_elem = textline.find(".//ns:TexEquiv/ns:Unicode", namespaces)
                text_coords = textline.find("ns:Coords", namespaces).attrib.get('points')
                unicode_elem = textline.find(".//ns:TextEquiv/ns:Unicode", namespaces)
                unicode_text = unicode_elem.text if unicode_elem is not None else ""
                # if unicode_elem.text is not None:
                #     unicode_text = unicode_elem.text
                # else:
                #     words = textline.findall(".//ns:Word/ns:TextEquiv/ns:Unicode", namespaces)
                #     unicode_text = " ".join(w.text for w in words if w.text)

                # unicode_text = unicode_elem.text if unicode_elem is not None else ""
                # print(unicode_text)
                # if text_coords:
                regions.append({'image_filename': image_filename, 'id': text_id, 'coords': text_coords, 'text': unicode_text})
        return regions
    
    except Exception as e:
        print(f"Failed processing get_text_regions {xml_file}: {e}")
        return []

In [41]:
# for eaa1980

def get_text_regions1(xml_file):
    try:
        tree = ET.parse(xml_file)
        root = tree.getroot()

        namespaces = {'ns': root.tag.split('}')[0].strip('{')}

        image_filename = root.findall(".//ns:sourceImageInformation/ns:fileName", namespaces).text

        regions = []

        for block in root.findall(".//ns:TextBlock", namespaces):

            for textline in block.findall(".//ns:TextBlock", namespaces):
                text_id = textline.get("id")

                text_coords = block.find("ns:Polygon", namespaces).get('POINTS')
                text = block.find(".//ns:TextLine/ns:String", namespaces).get('CONTENT')
                unicode_text = text if text is not None else ""

                regions.append({'image_filename': image_filename, 'id': text_id, 'coords': text_coords, 'text': unicode_text})
        return regions
    
    except Exception as e:
        print(f"Failed processing get_text_regions {xml_file}: {e}")
        return []

In [42]:
import cv2

def polygon_crop(image, points):
    try:
        if not points:
            return None

        mask = np.zeros(image.shape[:2], dtype=np.uint8)
        # points = np.array([list(map(int, p.split(','))) for p in points.split()], dtype=np.int32)
        points = np.array([tuple(map(int, p.split(','))) for p in points.split()], dtype=np.int32)
        if len(points) < 3:
            print("Not enough points", points)
        
        cv2.fillPoly(mask, [points], 255)

        res = cv2.bitwise_and(image, image, mask=mask)

        x, y, w, h = cv2.boundingRect(points)
        if w==0 or h==0:
            print("w or h is zero", w, h)
        cropped_img = res[y:y+h, x:x+w]
        return cropped_img
    
    except Exception as e:
        print(f"Failed processing polygon_crop: {e}")
        return None

In [43]:
def load_pil_cv2(image_path):
    '''
    cv2 doesn't read files with cyrillic names.
    Use PIL.
    '''
    img = Image.open(image_path).convert("RGB")
    img = np.array(img)
    return cv2.cvtColor(img, cv2.COLOR_RGB2BGR)


def process_images(image_dir, xml_dir, output_dir, output_csv):
    os.makedirs(output_dir, exist_ok=True)
    data = []

    for xml_file in os.listdir(xml_dir):
        xml_path = os.path.join(xml_dir, xml_file)
        
        text_lines = get_text_regions(xml_path)

        if not text_lines:
            continue  # pass an empty xml

        image_filename = text_lines[0]["image_filename"]
        image_path = os.path.join(image_dir, image_filename)

        if not os.path.exists(image_path):
            print(f"{image_path} does not exist")

        image = load_pil_cv2(image_path)
        if image is None:
            print("Image doesnt exist", image_path)
            continue

        for i, region in enumerate(text_lines):

            cropped_filename = f"{os.path.splitext(image_filename)[0]}_{i:02}.png"
            cropped_path = os.path.join(output_dir, cropped_filename)

            cropped_img = polygon_crop(image, region['coords'])

            if cropped_img is None or cropped_img.size == 0:
                print(f"Failed processing cropped {cropped_filename}_{i:02}.png")
                print(f"Cropped image is None: {cropped_img is None}")
                continue

            if region['text'] != "":
                _, encoded_img = cv2.imencode(".png", cropped_img)
                # cv2.imwrite(cropped_path, cropped_img)
                encoded_img.tofile(cropped_path)

                data.append({'filename': cropped_filename, 'text': region['text']})

    df = pd.DataFrame(data)
    return df
    # df.to_csv(output_csv, index=False, encoding="utf-8")

In [ ]:
# image_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/6470048"
# image_file = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/6470048/shchodennyk-0050.jpg"
# xml_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/6470048/page/shchodennyk-0050.xml"
# output_dir = os.path.join(image_dir, "cropped_test")
# output_csv = os.path.join(image_dir, "test.txt")
# os.makedirs(output_dir, exist_ok=True)

# data = []
# image = cv2.imread(image_file)
# if image is None:
#     print("image is None", image_file)

# text_regions = get_text_regions(xml_dir)

# for i, region in enumerate(text_regions):
#     cropped_img = polygon_crop(image, region['coords'])

#     if cropped_img is None or cropped_img.size == 0:
#         print(f"Failed processing test_{i:02}.png")
#         continue

#     filename = f"test_{i:02}.png"
#     save_path = os.path.join(output_dir, filename)
#     cv2.imwrite(save_path, cropped_img)

#     data.append({'filename': filename, 'text': region['text']})

# df = pd.DataFrame(data)
# df.to_csv(output_csv, index=False, encoding="utf-8")

## Dataset 6470048

In [ ]:
image_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/6470048/"
xml_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/6470048/page/"
output_dir = os.path.join(image_dir, "cropped_6470048")
output_csv = os.path.join(image_dir, "cropped_6470048.txt")
process_images(image_dir, xml_dir, output_dir, output_csv)

Failed processing Akhtyrs'ka-0002_00.png
Failed processing Akhtyrs'ka-0003_19.png
Failed processing Akhtyrs'ka-0004_00.png
Failed processing Letters_Shwedowa_11_2022-0001_00.png
Failed processing Letters_Shwedowa_11_2022-0015_00.png
Failed processing Letters_Shwedowa_11_2022-0032_00.png
Failed processing Letters_Shwedowa_11_2022-0040_00.png
Failed processing Letters_Shwedowa_11_2022-0042_00.png
Failed processing Letters_Shwedowa_11_2022-0042_01.png
Failed processing Letters_Shwedowa_11_2022-0042_02.png
Failed processing Letters_Shwedowa_11_2022-0043_00.png
Failed processing Letters_Shwedowa_11_2022-0043_01.png
Failed processing Moroz_Dudyk-0004_00.png
Failed processing Moroz_Dudyk-0004_17.png
Failed processing Moroz_Dudyk-0007_00.png
Failed processing Moroz_Dudyk-0007_04.png
Failed processing Moroz_Dudyk-0007_15.png
Failed processing Moroz_Dudyk-0009_00.png
Failed processing Moroz_Dudyk-0009_05.png
Failed processing Moroz_Dudyk-0009_06.png
Failed processing Moroz_Dudyk-0009_10.png
Fail

In [ ]:
# dataset = pd.read_csv("C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/6470048/cropped_6470048.txt", delimiter=",", header=None, names=["file_name", "text"], on_bad_lines="skip")
# dataset_prev = pd.read_csv("C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/6470048/tmp/cropped_6470048.txt", delimiter=",", header=None, names=["file_name", "text"], on_bad_lines="skip")

# old_text_dict = dict(zip(dataset_prev["file_name"], dataset_prev["text"]))
# dataset["text"] = dataset.apply(lambda row: old_text_dict.get(row["file_name"], row["text"]) if row["text"] == "" else row["text"], axis=1)
# dataset.to_csv("C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/6470048/df_crops_6470048.txt")

## Dataset 1365312

In [ ]:
image_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/"
xml_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/page/"
output_dir = os.path.join(image_dir, "cropped_1365312")
output_csv = os.path.join(image_dir, "cropped_1365312.txt")
df = process_images(image_dir, xml_dir, output_dir, output_csv)

# image_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/"
# xml_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/page/"
# output_dir = os.path.join(image_dir, "cropped_test")
# output_csv = os.path.join(image_dir, "cropped_test.txt")
# process_images(image_dir, xml_dir, output_dir, output_csv)


# data = []
# image = cv2.imread(os.path.join(image_dir, "4.jpg"))
# if image is None:
#     print("Image doesnt exist", os.path.join(image_dir, "4.jpg"))

# name = os.path.splitext("4")[0]
# xml_path = os.path.join(xml_dir, name + ".xml")

# text_regions = get_text_regions(xml_path)
# for i, region in enumerate(text_regions):
#     print(region['text'])


# for i, region in enumerate(text_regions):
#     cropped_img = polygon_crop(image, region['coords'])

#     if cropped_img is None or cropped_img.size == 0:
#         print(f"Failed processing cropped {name}_{i:02}.png")
#         print(f"Cropped image size: {cropped_img.size}")
#         print(f"Cropped image is None: {cropped_img is None}")
#         continue

#     filename = f"{name}_{i:02}.png"
#     save_path = os.path.join(output_dir, filename)
#     if not os.path.exists(save_path):
#         cv2.imwrite(save_path, cropped_img)

#     data.append({'filename': filename, 'text': region['text']})

# df = pd.DataFrame(data)
# df.to_csv(output_csv, index=False, encoding="utf-8")

In [68]:
image_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/"
df_to_clean = pd.read_csv(os.path.join(image_dir, "cropped_1365312old.txt"), delimiter=",", header=None, names=["file_name", "text"], on_bad_lines="skip")

In [69]:
def remove_not_existing(df, folder):
    df = df[df['file_name'].apply(lambda f: os.path.exists(os.path.join(folder, f)))]
    return df.reset_index(drop=True)

In [70]:
clean_df = remove_not_existing(df, "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/cropped_1365312")
output_csv = os.path.join(image_dir, "cropped_1365312.txt")
clean_df.to_csv(output_csv, index=False, encoding="utf-8")

In [71]:
from sklearn.model_selection import train_test_split

new_dataset = pd.read_csv(os.path.join(image_dir, "cropped_1365312.txt"), delimiter=",", header=None, names=["file_name", "text"], on_bad_lines="skip")

In [72]:
train_df, test_df = train_test_split(new_dataset, test_size=0.2, random_state=42)
train_df = train_df.reset_index(drop=True)
test_df = test_df.reset_index(drop=True)

In [73]:
train_df.head()

file_name            text
0  Скан_20190925_19 (4)_51.png      Господь? —
1          20190124 010_37.png     Жамбыльская
2          20190124 365_31.png  Карагандинская
3  Скан_20200310_25 (4)_30.png        и улыбки
4          20190124 077_04.png      Узбекистан

In [74]:
test_df.head()

file_name                                     text
0   Скан_20190925_31 (2)_21.png                        Последний потомок
1   Скан_20200310_16 (9)_51.png                        шестого чувства. 
2       Скан_20190925_34_24.png                                   Дремля
3        81131_01_03_027_20.png  сестёр милосердия Ел. Хрис. Черкасову и
4  Скан_20190925_10 (18)_45.png                                желаньем;

In [75]:
train_df.to_csv(os.path.join(image_dir, "1365312_train.txt"), index=False, encoding="utf-8")

In [76]:
test_df.to_csv(os.path.join(image_dir, "1365312_test.txt"), index=False, encoding="utf-8")

In [77]:
# split cropped images in different directories

test_images = f"{image_dir}1365312_test/"
train_images = f"{image_dir}1365312_train/"
os.makedirs(test_images, exist_ok=True)
os.makedirs(train_images, exist_ok=True)

for _, row in test_df.iterrows():
    os.rename(os.path.join(image_dir, "cropped_1365312/") + row['file_name'], test_images + row['file_name'])

for _, row in train_df.iterrows():
    os.rename(os.path.join(image_dir, "cropped_1365312/") + row['file_name'], train_images + row['file_name'])

In [78]:
from transformers import TrOCRProcessor

model = "microsoft/trocr-base-handwritten"
processor = TrOCRProcessor.from_pretrained(model)

processor.save_pretrained("cyrillic_seq2seq_trocr_21")

[]

In [80]:
mini_image_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/"

In [81]:
mini_dataset = pd.read_csv(os.path.join(mini_image_dir, "cropped_test.txt"), delimiter=",", header=None, names=["file_name", "text"], on_bad_lines="skip")
mini_train_df, mini_test_df = train_test_split(new_dataset, test_size=0.2, random_state=42)
mini_train_df = mini_train_df.reset_index(drop=True)
mini_test_df = mini_test_df.reset_index(drop=True)

In [82]:
mini_train_df.head()

file_name            text
0  Скан_20190925_19 (4)_51.png      Господь? —
1          20190124 010_37.png     Жамбыльская
2          20190124 365_31.png  Карагандинская
3  Скан_20200310_25 (4)_30.png        и улыбки
4          20190124 077_04.png      Узбекистан

In [83]:
mini_test_df.head()

file_name                                     text
0   Скан_20190925_31 (2)_21.png                        Последний потомок
1   Скан_20200310_16 (9)_51.png                        шестого чувства. 
2       Скан_20190925_34_24.png                                   Дремля
3        81131_01_03_027_20.png  сестёр милосердия Ел. Хрис. Черкасову и
4  Скан_20190925_10 (18)_45.png                                желаньем;

In [84]:
mini_train_df.to_csv(os.path.join(mini_image_dir, "minitrain.txt"), index=False, encoding="utf-8")
mini_test_df.to_csv(os.path.join(mini_image_dir, "minitest.txt"), index=False, encoding="utf-8")

In [ ]:
test_images = f"{mini_image_dir}test/"
train_images = f"{mini_image_dir}train/"
os.makedirs(test_images, exist_ok=True)
os.makedirs(train_images, exist_ok=True)

for _, row in mini_test_df.iterrows():
    os.rename(os.path.join(mini_image_dir, "cropped_test/") + row['file_name'], test_images + row['file_name'])

for _, row in mini_train_df.iterrows():
    os.rename(os.path.join(mini_image_dir, "cropped_test/") + row['file_name'], train_images + row['file_name'])

In [26]:
test_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/1365312_test/"
train_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/1365312_train/"
all_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/"

with open(all_dir + "1365312_test.txt", encoding="utf8") as f:
    for line in f.readlines():
        line = line.split(".png")[0]
        if os.path.exists(os.path.join(test_dir, line) + ".png"):
            print(f"{line} in {os.path.join(test_dir, line)}")
        else:
            print(f"{line} DOESNT EXIST in {os.path.join(test_dir, line)}")

with open(all_dir + "1365312_train.txt", encoding="utf8") as f:
    for line in f.readlines():
        line = line.split(".png")[0]
        if os.path.exists(os.path.join(train_dir, line) + ".png"):
            print(f"{line} in {os.path.join(train_dir, line)}")
        else:
            print(f"{line} DOESNT EXIST in {os.path.join(train_dir, line)}")

Скан_20200310_16 (9)_51 DOESNT EXIST in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/1365312_test/﻿Скан_20200310_16 (9)_51
Скан_20190925_34_24 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/1365312_test/Скан_20190925_34_24
81131_01_03_027_20 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/1365312_test/81131_01_03_027_20
Скан_20190925_10 (18)_45 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/1365312_test/Скан_20190925_10 (18)_45
20180417-1 008_38 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/1365312_test/20180417-1 008_38
Скан_20190925_15 (4)_35 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/1365312_test/Скан_20190925_15 (4)_35
100_3774_23 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/1365312/1365312_test/100_3774_23
Скан_20200310_18 (5)_36 in C:/Users/dhlabadmin/Desktop/m-test/ful

In [19]:
import os
import pathlib

# first test on the mini dataset

test_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/mini1365312/mini1365312_test/"
train_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/mini1365312/mini1365312_train/"
all_dir = "C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/mini1365312/"

with open(all_dir + "mini1365312_test.txt", encoding="utf8") as f:
    for line in f.readlines():
        line = line.split(".")[0]
        # a = os.path.join(test_dir, line) + ".png"
        a = pathlib.Path(test_dir + line + ".png")
        if a.exists():
            print(f"{line} in {os.path.join(test_dir, line)}\n")
        else:
            print(f"{line} DOESNT EXIST in {os.path.join(test_dir, line)}\n")

with open(all_dir + "mini1365312_train.txt", encoding="utf8") as f:
    for line in f.readlines():
        line = line.split(".")[0]
        b = os.path.join(train_dir, line) + ".png"
        if os.path.exists(b):
            print(f"{line} in {os.path.join(train_dir, line)}\n")
        else:
            print(f"{line} DOESNT EXIST in {os.path.join(train_dir, line)}\n")

Скан_20190925_31 (2)_21 DOESNT EXIST in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/mini1365312/mini1365312_test/﻿Скан_20190925_31 (2)_21

Скан_20200310_16 (9)_51 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/mini1365312/mini1365312_test/Скан_20200310_16 (9)_51

Скан_20190925_34_24 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/mini1365312/mini1365312_test/Скан_20190925_34_24

81131_01_03_027_20 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/mini1365312/mini1365312_test/81131_01_03_027_20

Скан_20190925_10 (18)_45 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/mini1365312/mini1365312_test/Скан_20190925_10 (18)_45

20180417-1 008_38 in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpacked-datasets/test/mini1365312/mini1365312_test/20180417-1 008_38

﻿Скан_20190925_19 (4)_51 DOESNT EXIST in C:/Users/dhlabadmin/Desktop/m-test/full-datasets/unpack

In [6]:
t = "Скан-20190925_19 (4)_51.png,Господь? —"
t=t.split(".")[0] + ".png"
print(t)

Скан-20190925_19 (4)_51.png
